In [1]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc




def add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder, ice_type):


    bins_bed = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.csv', names=['chr', 'start', 'end'])
    bins_bed['bin_id'] = bins_bed.index.tolist()

    bins_bed.to_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv', index=False, header=False, sep='\t')
    if species == 'human':

        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Human/hg38-blacklist.v2.bed'
    else:
        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Mouse/mm10-blacklist.v2.bed'

    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {blacklist_file} -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed")
    blacklist_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'c1', 'c2', 'c3', 'c4'])
    
    
    adata = ad.read_h5ad(f'{input_file_h5ad}')

    data = adata.X + 0.0
    
    if resolution == '1kbp_raw':
    
        data = data.astype('float32')
        
    elif resolution == '10kbp_raw':
    
        data = data.astype('float32')
    else:
        data = data.astype('float64')
        
    np_of_rows = len(adata.obs_names.tolist())
    np_of_col = len(adata.var_names.tolist())
        
    

        
    
    nan_columns = blacklist_bins['bin_id'].tolist()

    data[:, nan_columns] = np.nan


    chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()

    chrom_index_list  = {}
    for chrom in chr_list:
          st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
          en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
          chrom_index_list[chrom] = list(range(st, en+1))

    chrom_index_list_intra = {}
    for chrom in chr_list:
        index_list = []
        for chrom2 in chr_list:
            if chrom2 != chrom:
                index_list.extend(chrom_index_list[chrom2])

        chrom_index_list_intra[chrom] = index_list

    gtf = read_gtf(gene_annot_file)
    genes = gtf.df.loc[gtf.df['Feature'] == 'gene'].copy()
    genes['gene_id'] = [x.split('.')[0] for x in genes['gene_id']]
    genes['gene_id'].drop_duplicates(inplace=True)

    if not genes['Chromosome'].str.startswith('chr').any():
        genes['Chromosome'] = [f'chr{x}' for x in genes['Chromosome']]

    genes  = genes.set_index('gene_id')

    genes = genes.loc[adata.obs_names.tolist(), :]
    
    genes = genes.reset_index()



    genes[['Chromosome', 'Start', 'End', 'gene_id']].to_csv(f'{base_folder}hi_c_data_processing/data_{species}/gene_info.tsv', index=False, header=False, sep='\t')


    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {base_folder}hi_c_data_processing/data_{species}/gene_info.tsv -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv")
    gene_id_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'st', 'end', 'gene_id', 'c4'])

    
    if process_type == 'intra':

        layer_value_list = [0, 1, 10, 100, 1000]
        layer_name_list = ['intra']*len(layer_value_list)

    if process_type == 'inter':
        layer_name_list = ['inter']
        layer_value_list = [0]

    if process_type == 'gw':
        layer_value_list = [0, 1, 10, 100, 1000]
        layer_name_list = ['intra']*len(layer_value_list)
        layer_name_list.append('inter')
        layer_value_list.append(0)



    for layer_type, dist in zip(layer_name_list, layer_value_list):
        
            adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
        
            new_layer_name = f'{process_type}_{layer_type}_{dist}'
        
        #if new_layer_name in adata.layers:
        #    continue
        #else:

            mask = np.zeros_like(data, dtype=bool)

        

            for index, row in genes.iterrows():

                if layer_type == 'intra':
                    columns_to_mask = chrom_index_list_intra[row['Chromosome']]
                else:
                    columns_to_mask = chrom_index_list[row['Chromosome']]

                mask[index, columns_to_mask] = True

                if layer_type == 'intra':

                    start_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].min()

                    end_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].max()

                    mask[index, start_index:end_index+1]  = True

                    #for idx in [start_index, end_index]:
                    mask[index, max(0, start_index - dist):min(data.shape[1], end_index + dist+1)] = True




            data_layered = np.where(mask, np.nan, data)



            layer_name = f'{layer_type}_{dist}_raw'

            adata_l.layers[layer_name] = data_layered

            z_scores = stats.zscore(data_layered, axis=1, nan_policy='omit')


            clipped_z_scores = np.clip(z_scores, -10, 10)



            layer_name = f'{layer_type}_{dist}_z_scores'

            adata_l.layers[layer_name] = clipped_z_scores



            del z_scores
            del clipped_z_scores
            gc.collect()

            #data_plus_one = data_layered + 1

            #log_transformed_data = np.log1p(data_plus_one)

            del data_layered
            #del data_plus_one
            gc.collect()

            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed'

            #adata.layers[layer_name] = log_transformed_data

            #z_scores = stats.zscore(log_transformed_data, axis=1, nan_policy='omit')

            #clipped_z_scores = np.clip(z_scores, -10, 10)



            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed_z_scores'

            #adata.layers[layer_name] = clipped_z_scores

            #del z_scores
            #del log_transformed_data
            #del clipped_z_scores
            #gc.collect()
            adata_l.obs_names = adata.obs_names.tolist()
            adata_l.var_names = adata.var_names.tolist()
            
            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{layer_name}_by_allbins_max.h5ad'
            
            

            adata_l.write(outputfile_h5ad, compression="gzip")
            
            

INFO:numexpr.utils:Note: detected 192 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 192 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [34]:
base_folder = '/grid/gillis/data_norepl/lohia/'
species='mouse'
resolution='500kbp_raw'
SRP_name='aggregates'
process_type='intra'
ice_type='KR'
input_file_h5ad=f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_by_allbins_max.h5ad'
if species=='mouse':
    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
else:
    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 






In [ ]:
for species in ['human', 'mouse']:
    for process_type in ['intra']:
        for resolution in ['10kbp_raw', '1kbp_raw']:
            base_folder = '/grid/gillis/data_norepl/lohia/'
            SRP_name='aggregates'
            ice_type='KR'
            input_file_h5ad=f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_by_allbins_max.h5ad'
            if species=='mouse':
                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
            else:
                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
            add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder, ice_type)





In [37]:

add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder, ice_type)


In [39]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc

# Assuming your data is organized as NumPy arrays
# gene_observation_matrix is genesXobservations
# gene_category_matrix is genesXcategories
# Both matrices are NumPy arrays

# Example gene_observation_matrix (5 genes, 3 observations) with NaN values


# Calculate the mean of genes for each category and observation, ignoring NaN values
def calculate_category_means_ignore_nan(gene_observation_matrix_df, gene_category_matrix_df):
    # Calculate mean for each category (axis=0) and each observation (axis=1), ignoring NaN values


    genes_intersect = gene_observation_matrix_df.index.intersection(gene_category_matrix_df.index)

    gene_observation_matrix_df =  gene_observation_matrix_df.loc[genes_intersect, :]
    gene_category_matrix_df = gene_category_matrix_df.loc[genes_intersect, :]

    gene_observation_matrix = gene_observation_matrix_df.values
    gene_category_matrix = gene_category_matrix_df.values

    category_counts = np.dot(gene_category_matrix.T, ~np.isnan(gene_observation_matrix))
    
    gene_observation_matrix_cleaned = np.nan_to_num(gene_observation_matrix, nan=0.0)
    
    category_sums = np.dot(gene_category_matrix.T, gene_observation_matrix_cleaned)
    
    # Calculate mean using only non-NaN values
    category_means = category_sums / category_counts
    
    # Replace NaN values in category_means with 0 where division by 0 occurred
    #category_means[np.isnan(category_means)] = 0.0
    
    return category_means, category_counts

# Call the function to calculate category means, ignoring NaN values


def calc_marker_matrix(marker_list,gene_list, no_of_markers=10,  drop_duplicates=True, shuffle_labels=False):
    
        
        marker_list = marker_list[marker_list['Ensembl_gene_identifier'].isin(gene_list)]

        marker_list = marker_list.sort_values(by=['rank']).drop_duplicates(subset=['cell_type', 'gene'])
        
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()

        marker_list_list = []
        for group2 in all_cell_types:
                    m_tmp = marker_list[marker_list['cell_type']==group2].sort_values(by=['rank'])
                    m_tmp['rank_missing_gene'] = [x+1 for x in range(m_tmp.shape[0])]

                    marker_list_list.append(m_tmp)

        marker_list = pd.concat(marker_list_list)

        marker_list = marker_list[marker_list['rank_missing_gene']<=no_of_markers]

        marker_list['%recurrence'] = marker_list['recurrence'] / marker_list['n_datasets']
        marker_list['%recurrence'] = 1/marker_list['%recurrence']
        
        marker_list_copy = marker_list.copy()
        

        


        if drop_duplicates==True:

            marker_list = marker_list.sort_values(by=['rank', '%recurrence', 'auroc', 'rank_missing_gene']).drop_duplicates(subset=['Ensembl_gene_identifier'], keep=False)
        elif drop_duplicates=="one_copy":
            marker_list = marker_list.sort_values(by=['rank', '%recurrence', 'auroc', 'rank_missing_gene']).drop_duplicates(subset=['Ensembl_gene_identifier'])
        else:
            pass
        
        if shuffle_labels == True:
            

            shuffled_Ensembl_gene_identifier = marker_list['Ensembl_gene_identifier'].sample(frac=1, replace=False, random_state=42).reset_index(drop=True)


            marker_list['Ensembl_gene_identifier'] = shuffled_Ensembl_gene_identifier.tolist()
            
        else:
            pass


        df2_list = []
        for group2 in all_cell_types:
                    
                    m_tmp = marker_list[marker_list['cell_type']==group2]
                    #if number_of_times == 1:
                    df2_list.append(m_tmp)
                    #else:
                    #    random_indices = np.random.choice(m_tmp.index, size=bootstarp_size, replace=True)
                    #    bootstrap_sample = m_tmp.loc[random_indices]
                    #    df2_list.append(bootstrap_sample)

        marker_list=pd.concat(df2_list)
        marker_list_copy['rank'] = 0
        marker_list = pd.concat([marker_list, marker_list_copy])
        
        

        marker_table = marker_list.pivot_table(index='Ensembl_gene_identifier', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)

        marker_table[marker_table != 0] = 1

        

        return marker_table
        

#for each marker-list and input file , I can make one output file

def calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name):

        marker_list= pd.read_csv(f'{base_folder}/hi_c_data_processing/{species}_{marker_name}.csv')
        cell_type_order = marker_list['cell_type'].drop_duplicates().tolist()



        
        

        adata = ad.read_h5ad(f'{input_file_h5ad}')
        
        np_of_col = adata.X.shape[1]
        np_of_rows = len(cell_type_order)
        
        #adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
        
        layer_names = adata.layers.keys()
        no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,26,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,318,356,400,446,500]     
        for no_of_markers in no_of_markers_list:
            for drop_duplicates in [False, True]:
                    for shuf in [True, False]:
                        for given_layer in layer_names:
                            
                                adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))

                                gene_list = adata.obs_names.tolist()

                                gene_observation_matrix_dataframe = adata.to_df(layer=given_layer)

                                gene_category_dataframe = calc_marker_matrix(marker_list, gene_list, no_of_markers=no_of_markers,  drop_duplicates=drop_duplicates, shuffle_labels=shuf)

                                gene_category_dataframe = gene_category_dataframe.loc[:,cell_type_order]

                                category_means, category_counts = calculate_category_means_ignore_nan(gene_observation_matrix_dataframe, gene_category_dataframe)

                                l_n = f'mean'

                                adata_l.layers[l_n] = category_means

                                l_n = f'counts'

                                adata_l.layers[l_n] = category_counts
                                
                                #z_scores = stats.zscore(category_means, axis=0, nan_policy='omit')
                                #l_n = f'{given_layer}_{no_of_markers}_{drop_duplicates}_{shuf}_mean_scaled'
                                #adata_l.layers[l_n] = z_scores
                                
                                #z_scores = stats.zscore(category_counts, axis=0, nan_policy='omit')
                                #l_n = f'{given_layer}_{no_of_markers}_{drop_duplicates}_{shuf}_counts_scaled'
                                #adata_l.layers[l_n] = z_scores


                                adata_l.obs_names = cell_type_order
                                adata_l.var_names = adata.var_names.tolist()
                                
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{no_of_markers}_by_allbins_max_mean.h5ad'

                                adata_l.write(outputfile_h5ad, compression="gzip")








In [ ]:

calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, outputfile_h5ad)

In [ ]:
base_folder = '/grid/gillis/data_norepl/lohia/'
species='mouse'
resolution='500kbp_raw'
SRP_name='aggregates'
process_type='intra'
ice_type='KR'
input_file_h5ad=f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_by_allbins_max.h5ad'
if species=='mouse':
    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
else:
    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
    
    


dist=0
layer_name = z_scores
input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_by_allbins_max.h5ad'


marker_name = 'brain_class'


calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)


<ipython-input-39-2654b5369092>:56: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-39-2654b5369092>:56: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-39-2654b5369092>:56: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-39-2654b5369092>:56: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-39-2654b5369092>:56: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-39-2654b5369092>:56: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-39-2654b5369092>:56: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category

In [1]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc

INFO:numexpr.utils:Note: detected 192 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 192 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [5]:
base_folder = '/grid/gillis/data_norepl/lohia/'
species='mouse'
resolution='1kbp_raw'
SRP_name='aggregates'
input_file_h5ad='/grid/gillis/data_norepl/lohia/hi_c_data_processing/data_mouse/aggregates/1kbp_raw/max/hic_gene_gw_none_by_allbins_max.h5ad'
gene_annot_file='/grid/gillis/data_norepl/lohia/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
process_type='gw'

In [6]:
    bins_bed = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.csv', names=['chr', 'start', 'end'])
    bins_bed['bin_id'] = bins_bed.index.tolist()

    bins_bed.to_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv', index=False, header=False, sep='\t')
    if species == 'human':

        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Human/hg38-blacklist.v2.bed'
    else:
        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Mouse/mm10-blacklist.v2.bed'

    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {blacklist_file} -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed")
    blacklist_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'c1', 'c2', 'c3', 'c4'])
    

In [9]:
adata = ad.read_h5ad(f'/grid/gillis/data_norepl/lohia/hi_c_data_processing/data_mouse/aggregates/1kbp_raw/max/hic_gene_intra_KR_by_allbins_max.h5ad')



In [4]:
    data = adata.X + 0.0
    
    if resolution == '1kbp_raw':
    
        data = data.astype('float32')
        
    elif resolution == '10kbp_raw':
    
        data = data.astype('float32')
    else:
        data = data.astype('float64')

        
    
    nan_columns = blacklist_bins['bin_id'].tolist()

    data[:, nan_columns] = np.nan


    chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()

    chrom_index_list  = {}
    for chrom in chr_list:
          st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
          en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
          chrom_index_list[chrom] = list(range(st, en+1))

    chrom_index_list_intra = {}
    for chrom in chr_list:
        index_list = []
        for chrom2 in chr_list:
            if chrom2 != chrom:
                index_list.extend(chrom_index_list[chrom2])

        chrom_index_list_intra[chrom] = index_list

    gtf = read_gtf(gene_annot_file)
    genes = gtf.df.loc[gtf.df['Feature'] == 'gene'].copy()
    genes['gene_id'] = [x.split('.')[0] for x in genes['gene_id']]
    genes['gene_id'].drop_duplicates(inplace=True)

    if not genes['Chromosome'].str.startswith('chr').any():
        genes['Chromosome'] = [f'chr{x}' for x in genes['Chromosome']]

    genes  = genes.set_index('gene_id')

    genes = genes.loc[adata.obs_names.tolist(), :]
    
    genes = genes.reset_index()



    genes[['Chromosome', 'Start', 'End', 'gene_id']].to_csv(f'{base_folder}hi_c_data_processing/data_{species}/gene_info.tsv', index=False, header=False, sep='\t')


    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {base_folder}hi_c_data_processing/data_{species}/gene_info.tsv -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv")
    gene_id_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'st', 'end', 'gene_id', 'c4'])

    


NameError: name 'adata' is not defined

In [14]:
    if process_type == 'intra':

        layer_value_list = [0, 1, 10, 100, 1000]
        layer_name_list = ['intra']*len(layer_value_list)

    if process_type == 'inter':
        layer_name_list = ['inter']
        layer_value_list = [0]

    if process_type == 'gw':
        layer_value_list = [0, 1, 10, 100, 1000]
        layer_name_list = ['intra']*len(layer_value_list)
        layer_name_list.append('inter')
        layer_value_list.append(0)



    for layer_type, dist in zip(layer_name_list, layer_value_list):
        
        new_layer_name = f'{process_type}_{layer_type}_{dist}'
        
        if new_layer_name in adata.layers:
            continue
        else:

            mask = np.zeros_like(data, dtype=bool)

        

            for index, row in genes.iterrows():

                if layer_type == 'intra':
                    columns_to_mask = chrom_index_list_intra[row['Chromosome']]
                else:
                    columns_to_mask = chrom_index_list[row['Chromosome']]

                mask[index, columns_to_mask] = True

                if layer_type == 'intra':

                    start_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].min()

                    end_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].max()

                    mask[index, start_index:end_index+1]  = True

                    #for idx in [start_index, end_index]:
                    mask[index, max(0, start_index - dist):min(data.shape[1], end_index + dist+1)] = True




            data_layered = np.where(mask, np.nan, data)



            layer_name = f'{process_type}_{layer_type}_{dist}'

            adata.layers[layer_name] = data_layered

            z_scores = stats.zscore(data_layered, axis=1, nan_policy='omit')


            clipped_z_scores = np.clip(z_scores, -10, 10)



            layer_name = f'{process_type}_{layer_type}_{dist}_z_scores'

            adata.layers[layer_name] = clipped_z_scores



            del z_scores
            del clipped_z_scores
            gc.collect()

            #data_plus_one = data_layered + 1

            #log_transformed_data = np.log1p(data_plus_one)

            del data_layered
            #del data_plus_one
            gc.collect()

            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed'

            #adata.layers[layer_name] = log_transformed_data

            #z_scores = stats.zscore(log_transformed_data, axis=1, nan_policy='omit')

            #clipped_z_scores = np.clip(z_scores, -10, 10)



            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed_z_scores'

            #adata.layers[layer_name] = clipped_z_scores

            #del z_scores
            #del log_transformed_data
            #del clipped_z_scores
            #gc.collect()

            adata.write(f'{input_file_h5ad}', compression="gzip")

RuntimeError: Can't get creation plist (bad object header version number)

Above error raised while writing key 'gw_intra_0' of <class 'h5py._hl.group.Group'> to /

In [ ]:
if [[ "$species" == "human" ]]
then
CHROMS=/grid/gillis/data_norepl/nfox/genomes/homo_sapiens_38/hg38.chrom.sizes 
chrom_list="chr1,chr2,chr3,chr4,chr5,chr6,chr7,chr8,chr9,chr10,chr11,chr12,chr13,chr14,chr15,chr16,chr17,chr18,chr19,chr20,chr21,chr22"
chrom_list_2="chr1 chr2 chr3 chr4 chr5 chr6 chr7 chr8 chr9 chr10 chr11 chr12 chr13 chr14 chr15 chr16 chr17 chr18 chr19 chr20 chr21 chr22"
GENOME="gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz"
EXP_NETWORKS="human_prioAggNet.hdf5"

elif [[ "$species" == "mouse" ]]
then
CHROMS=/grid/gillis/data_norepl/nfox/genomes/mus_musculus_10/mm10.chrom.sizes
GENOME="Mus_musculus.GRCm38.94.gtf.gz"
EXP_NETWORKS="mouse_prioAggNet.hdf5"
chrom_list="chr1,chr2,chr3,chr4,chr5,chr6,chr7,chr8,chr9,chr10,chr11,chr12,chr13,chr14,chr15,chr16,chr17,chr18,chr19"
chrom_list_2="chr1 chr2 chr3 chr4 chr5 chr6 chr7 chr8 chr9 chr10 chr11 chr12 chr13 chr14 chr15 chr16 chr17 chr18 chr19"


In [ ]:
add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder)



In [ ]:

ice_type='none'

base_path='/grid/gillis/data_norepl/lohia/'


        
    python ${software_path}/add_contact_norm_layers.py \
    --process_type ${process} \
    --species ${species} \
    --input_file_h5ad /grid/gillis/data_norepl/lohia/hi_c_data_processing/data_mouse/aggregates/10kbp_raw/max/hic_gene_gw_none_by_allbins_max.h5ad \
    --base_path $base_path \
    --resolution $NETWORK \
    --SRP $SRP_name \
    --gene_annot_file ${base_folder}/lohia/hi_c_data_processing/genomes_jlee/${GENOME}
    

